# Downstream Analysis -- feature annotation
### Introduction

In this case study, we process a MALDI-TIMS-MS1 lipids dataset of mouse skin tissue, extract features with m/z and ion mobility, then convert ion mobility into collision cross section(CCS), and annotate features by looking up m/z and CCS in CCS compendium.

In [1]:
import timsimaging

# enable visualization in the Jupyter notebook
from bokeh.io import show, output_notebook
output_notebook()
# disable FutureWarning
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

Loading BokehJS ...

In [2]:
bruker_d_folder_name = r"D:\dataset\Melanie\MF402upper.d"
dataset = timsimaging.spectrum.MSIDataset(bruker_d_folder_name)
dataset

100%|██████████████████████████████████████████████████████████████████████████| 65052/65052 [00:13<00:00, 4783.46it/s]


MSIDataset with 65052 pixels
        mz range: 299.999-1350.004
        mobility range: 0.700-1.960
        

In [3]:
dataset.image()

### Peak processing
First we run the processing workflow to get the feature list. There are 3 columns in the result: m/z, ion mobility and intensity. The ion mobility is in $1/K_0$ (inverse reduced mobility), of which the unit is $V\cdotp s\cdotp cm^{-2}$

In [4]:
results = dataset.process(sampling_ratio=0.1, frequency_threshold=0.02, tolerance=3, adaptive_window=True, visualize=False)
peak_list = results["peak_list"]
peak_list

Computing mean spectrum...
Traversing graph...
Finding local maxima...
Summarizing...


100%|████████████████████████████████████████████████████████████████████████████████| 930/930 [02:41<00:00,  5.77it/s]


mz_values  mobility_values  total_intensity
1     302.058416         0.906070        28.807071
2     303.065771         0.907390       273.366334
3     303.065934         1.076893        73.819985
4     303.065516         0.948773         8.603689
5     304.069069         0.906924         3.887010
..           ...              ...              ...
926  1253.899905         1.844601        14.027978
927  1255.913279         1.853024        26.725288
928  1281.929607         1.870141        25.601230
929  1283.943538         1.877011         2.597694
930  1298.554342         1.759565         7.082859

[930 rows x 3 columns]

### Converting ion mobility into CCS
However, $1/K_0$ depends on the ion mobility technique and instrument. The data was collected by trapped ion mobility spectrometry(TIMS) while most ion mobility databases are from drift tube(DTIMS), to allow cross-platform comparison, we need to convert ion mobility into CCS, a property only depends on the ion itself. 

TIMSImaging converts $1/K_0$ into CCS by a linear model fitted with reference ion mobilities of calibrants. The metadata of calibration is stored in the raw data:

In [5]:
dataset.cali_info

KeyPolarity  \
KeyName                                           
CalibrationDateTime                           +   
CalibrationUser                               +   
CalibrationSoftware                           +   
CalibrationSoftwareVersion                    +   
MzCalibrationMode                             +   
MzStandardDeviationPPM                        +   
ReferenceMassList                             +   
MzCalibrationSpectrumDescription              +   
ReferenceMassPeakNames                        +   
ReferencePeakMasses                           +   
MeasuredTimesOfFlight                         +   
MeasuredMassPeakIntensities                   +   
MassesPreviousCalibration                     +   
MassesCorrectedCalibration                    +   
MobilityCalibrationDateTime                   +   
MobilityCalibrationUser                       +   
MobilityStandardDeviationPercent              +   
ReferenceMobilityList                         +   
CalibrationMobilogramDescription              +   
ReferenceMobilityPeakNames                    +   
ReferencePeakMobilities                       +   
MeasuredTimsVoltages                          +   
MeasuredMobilityPeakIntensities               +   
MobilitiesPreviousCalibration                 +   
MobilitiesCorrectedCalibration                +   
MobilitiyReferencePressure                    +   
MobilitiyPressureCompensationFactor           +   

                                                                                 Value  
KeyName                                                                                 
CalibrationDateTime                                          2024-07-28T12:37:35+02:00  
CalibrationUser                                                                unknown  
CalibrationSoftware                                                            timsTOF  
CalibrationSoftwareVersion                                                       5.1.8  
MzCalibrationMode                                                                    4  
MzStandardDeviationPPM                                                        0.209581  
ReferenceMassList                                   RedP_0_to_2000 07-03-2024 New List  
MzCalibrationSpectrumDescription                                             <unknown>  
ReferenceMassPeakNames               b'p3\x00p5\x00p9\x00p17\x00p21\x00p25\x00p29\x...  
ReferencePeakMasses                  b'\x17\xd9\xce\xf7S"\x8a@\xc5 \xb0r\xe8\x11\x8...  
MeasuredTimesOfFlight                b'!\xe8\xa9\xb9\x14\x0c\xf2@e\xaeo\xd5\x7f\xb3...  
MeasuredMassPeakIntensities          b'\x00\x00\x00\x00\x80<\xc6@\x00\x00\x00\x00\x...  
MassesPreviousCalibration            b'\xe0\xf4\xb4cY"\x8a@\xd79uE\xec\x11\x8c@\x7f...  
MassesCorrectedCalibration           b'\x962\xe9BT"\x8a@B\x8e\xd8\xe1\xe7\x11\x8c@\...  
MobilityCalibrationDateTime                                  2024-07-27T13:42:36+02:00  
MobilityCalibrationUser                                                        unknown  
MobilityStandardDeviationPercent                                              0.175188  
ReferenceMobilityList                           Tuning Mix ES-TOF CCS compendium (ESI)  
CalibrationMobilogramDescription                                             <unknown>  
ReferenceMobilityPeakNames           b'C6H19N3O6P3\x00C12H19F12N3O6P3\x00C18H19F24N...  
ReferencePeakMobilities              b'\xbe\xa3\x80$\x12\x90\xe7?\x00\xa0\xefq\x07\...  
MeasuredTimsVoltages                 b':\xe9\xb9o{uY@\x9d\xa9\x10\x8a\x9ada@\x8a:0,...  
MeasuredMobilityPeakIntensities      b'\x0eJ\x96\x80\x13\xe1CA\xdce\xc5&\xb0\x9feA\...  
MobilitiesPreviousCalibration        b'\x8a^\x97]\xd1\x9e\xe7?\xfd\xdap2s\xd5\xef?\...  
MobilitiesCorrectedCalibration       b'\xb5\x1aw\xe9\xb5\x8c\xe7?"d\xaaG\x9a\xc6\xe...  
MobilitiyReferencePressure                                                    2.195872  
MobilitiyPressureCompensationFactor                             

Compute CCS. We also have an option to call interal CCS conversion function from Bruker's TDFSDK API. Here we compute CCS in both methods.

In [6]:
ccs_linear_model = dataset.ccs_calibrator(method="linear")
peak_list["CCS_linear"] = ccs_linear_model.transform(peak_list["mz_values"], peak_list["mobility_values"], charge=1)
ccs_bruker_model = dataset.ccs_calibrator(method="internal")
peak_list["CCS_bruker"] = ccs_bruker_model.transform(peak_list["mz_values"], peak_list["mobility_values"], charge=1)
peak_list["Delta"] = (peak_list["CCS_bruker"]-peak_list["CCS_linear"])/peak_list["CCS_bruker"]

In [7]:
peak_list

mz_values  mobility_values  total_intensity  CCS_linear  CCS_bruker  \
1     302.058416         0.906070        28.807071  189.238376  189.666498   
2     303.065771         0.907390       273.366334  189.489590  189.916152   
3     303.065934         1.076893        73.819985  225.188273  225.393028   
4     303.065516         0.948773         8.603689  198.205047  198.577456   
5     304.069069         0.906924         3.887010  189.364654  189.791992   
..           ...              ...              ...         ...         ...   
926  1253.899905         1.844601        14.027978  374.204010  373.482918   
927  1255.913279         1.853024        26.725288  375.913545  375.181832   
928  1281.929607         1.870141        25.601230  379.316539  378.563683   
929  1283.943538         1.877011         2.597694  380.709363  379.947853   
930  1298.554342         1.759565         7.082859  356.744077  356.131468   

        Delta  
1    0.002257  
2    0.002246  
3    0.000908  
4    0.001875  
5    0.002252  
..        ...  
926 -0.001931  
927 -0.001950  
928 -0.001989  
929 -0.002004  
930 -0.001720  

[930 rows x 6 columns]

The results from TIMSImaging are almost the same with those from Bruker's method.

### Query features against CCS database
Now we can search m/z and CCS in a database to obtain putative feature annotation. Here we use CCS compendium, which could be downloaded from https://mcleanresearchgroup.shinyapps.io/CCS-Compendium

In [8]:
import pandas as pd
def query_feature(mz, ccs, i, library, ppm_tol=20, ccs_tol=5):

    columns = ['Compound', 'Neutral.Formula', 'CAS',
        'Theoretical.mz', 'Ion.Species', 'Charge',
        'CCS', 'Super.Class',
        'Class', 'Subclass']
    # ppm window
    mz_tol = mz * ppm_tol * 1e-6
    mz_min, mz_max = mz - mz_tol, mz + mz_tol
    
    ccs_min, ccs_max = ccs - ccs_tol, ccs + ccs_tol
    hit_index =  (library['mz'].between(mz_min, mz_max)) & (library['CCS'].between(ccs_min, ccs_max))
    # candidate subset by adduct and mz
    hits = library.loc[hit_index, columns].copy()
    hits["feature_id"] = i
    hits["measured_mz"] = mz
    hits["measured_CCS"] = ccs
    hits["ppm_error"] = (hits["Theoretical.mz"] - mz) / mz * 1e6
    hits["ccs_dev_%"] = ((hits["CCS"] - ccs) / ccs).abs() * 100

    if hits.empty:
        return pd.DataFrame()
    return hits


To save time, we search against a subset of the database: lipids with +1 charge state:

In [12]:
library = pd.read_csv(r"D:\dataset\UnifiedCCSCompendium_FullDataSet_2025-07-28.csv")
lipids_lib = library.loc[
    (library["Super.Class"]=="Lipids and lipid-like molecules")&
    (library["Charge"]==1)
    ]
lipids_lib

Compound Neutral.Formula           CAS  \
1045                     5-iPF2alpha-VI        C20H34O5   180469-63-0   
1047  8-iso-15(R)-Prostaglandin F2alpha        C20H34O5   214748-65-9   
1049        8-iso-Prostaglandin F2alpha        C20H34O5    27415-26-5   
1051        15(R)-Prostaglandin F2alpha        C20H34O5    37658-84-7   
1053      11-beta-Prostaglandin F2alpha        C20H34O5    38432-87-0   
...                                 ...             ...           ...   
3666                       Progesterone        C21H30O2       57-83-0   
3668       17-alpha-Hydroxyprogesterone        C21H30O3       68-96-2   
3669       17-alpha-Hydroxyprogesterone        C21H30O3       68-96-2   
3670        d7-Cholesterol Ester (18:1)      C45H71D7O2  1416275-35-8   
3671              Cholesteryl Palmitate        C43H76O2      601-34-3   

                                                  InChi  \
1045  InChI=1S/C20H34O5/c1-2-3-4-5-6-7-10-16-17(19(2...   
1047  InChI=1S/C20H34O5/c1-2-3-6-9-15(21)12-13-17-16...   
1049  InChI=1S/C20H34O5/c1-2-3-6-9-15(21)12-13-17-16...   
1051  InChI=1S/C20H34O5/c1-2-3-6-9-15(21)12-13-17-16...   
1053  InChI=1S/C20H34O5/c1-2-3-6-9-15(21)12-13-17-16...   
...                                                 ...   
3666  InChI=1S/C21H30O2/c1-13(22)17-6-7-18-16-5-4-14...   
3668  InChI=1S/C21H30O3/c1-13(22)21(24)11-8-18-16-5-...   
3669  InChI=1S/C21H30O3/c1-13(22)21(24)11-8-18-16-5-...   
3670  InChI=1S/C45H78O2/c1-7-8-9-10-11-12-13-14-15-1...   
3671  InChI=1S/C43H76O2/c1-7-8-9-10-11-12-13-14-15-1...   

                         InChiKey  Theoretical.mz        mz Ion.Species  \
1045  RZCPXIZGLPAGEV-UHFFFAOYSA-N        377.2304  377.2304      [M+Na]   
1047  PXGPLTODNUVGFL-PGWUFSIFSA-N        377.2304  377.2304      [M+Na]   
1049  PXGPLTODNUVGFL-NAPLMKITSA-N        377.2304  377.2304      [M+Na]   
1051  PXGPLTODNUVGFL-CKXCCYAOSA-N        377.2304  377.2304      [M+Na]   
1053  PXGPLTODNUVGFL-ZWAKLXPCSA-N        377.2304  377.2304      [M+Na]   
...                           ...             ...       ...         ...   
3666  RJKFOVLPORLFTN-LEKSSAKUSA-N        337.2144  337.2143      [M+Na]   
3668  DBPWSSGDRRHUNT-CEGNMAFCSA-N        331.2273  331.2273       [M+H]   
3669  DBPWSSGDRRHUNT-CEGNMAFCSA-N        353.2093  353.2093      [M+Na]   
3670  RJECHNNFRHZQKU-IHPCOYDHSA-N        680.6339  680.6305      [M+Na]   
3671  BBJQPKLGPMQWBU-JADYGXMDSA-N        647.5743  647.5704      [M+Na]   

     Ion.Species.Agilent  Charge  ... Rep5  Rep6  Rep7  Rep8  Rep9  Rep10  \
1045             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
1047             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
1049             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
1051             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
1053             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
...                  ...     ...  ...  ...   ...   ...   ...   ...    ...   
3666             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
3668              (M+H)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
3669             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
3670             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   
3671             (M+Na)+       1  ...  NaN   NaN   NaN   NaN   NaN    NaN   

     Rep11 Rep12 Rep13 Rep14  
1045   NaN   NaN   NaN   NaN  
1047   NaN   NaN   NaN   NaN  
1049   NaN   NaN   NaN   NaN  
1051   NaN   NaN   NaN   NaN  
1053   NaN   NaN   NaN   NaN  
...    ...   ...   ...   ...  
3666   NaN   NaN   NaN   NaN  
3668   NaN   NaN   NaN   NaN  
3669   NaN   NaN   NaN   NaN  
3670   NaN   NaN   NaN   NaN  
3671   NaN   NaN   NaN   NaN  

[664 rows x 37 columns]

Query features with m/z tolerance=20 ppm and CCS tolerance=5 $\mathring{A}^2$:

In [10]:
all_results = []
for i, feat in peak_list.iterrows():
    all_results.append(query_feature(feat['mz_values'], feat['CCS_linear'], i, lipids_lib, ppm_tol=20, ccs_tol=5))

In [11]:
final_results = pd.concat([r for r in all_results if not r.empty],
                              ignore_index=True) if any(not r.empty for r in all_results) else pd.DataFrame()
final_results

Compound Neutral.Formula  \
0                                       LysoPC (13:0)      C21H44NO7P   
1                                  Lithocholyltaurine      C26H45NO5S   
2                                       LysoPC (16:0)      C24H50NO7P   
3                                       LysoPC (18:1)      C26H52NO7P   
4     1,2-Didecanoyl-sn-glycero-3-phosphoethanolamine      C25H50NO8P   
5                                       LysoPC (18:0)      C26H54NO7P   
6                                     LysoPC (2-18:0)      C26H54NO7P   
7                          Platelet-activating Factor      C26H54NO7P   
8                                       LysoPC (19:0)      C27H56NO7P   
9                                      PC (17:0/02:0)      C27H56NO7P   
10                                      LysoPC (18:1)      C26H52NO7P   
11                                      LysoPC (18:0)      C26H54NO7P   
12                                    LysoPC (2-18:0)      C26H54NO7P   
13                         Platelet-activating Factor      C26H54NO7P   
14                                     PC (16:0E/2:0)      C26H54NO7P   
15                                      LysoPC (20:0)      C28H58NO7P   
16                                    PC (O-18:0/2:0)      C28H58NO7P   
17          1,2-Dilauroyl-sn-glycero-3-phosphocholine      C32H64NO8P   
18                                          Cer 42:02       C42H81NO3   
19                                          Cer 42:01       C42H83NO3   
20          1,2-Dilauroyl-sn-glycero-3-phosphocholine      C32H64NO8P   
21                                       PE (O-32:01)      C37H74NO7P   
22                          PC (16:1/16:1) (del9-cis)      C40H76NO8P   
23        1,2-Dipalmitoyl-sn-glycero-3-phosphocholine      C40H80NO8P   
24                                           SM 36:01     C41H83N2O6P   
25  1-Palmitoyl-2-oleoyl-sn-glycero-3-phosphoethan...      C39H76NO8P   
26                                           PE 34:01      C39H76NO8P   
27  1,2-Diheptadecanoyl-sn-glycero-3-phosphoethano...      C39H78NO8P   
28                                           PE 34:01      C39H76NO8P   
29        1,2-Dipalmitoyl-sn-glycero-3-phosphocholine      C40H80NO8P   
30                                 PC (18:1(9Z)/16:0)      C42H82NO8P   
31                           Di(2-ethylhexyl) adipate        C22H42O4   
32                                           PE 36:03      C41H76NO8P   
33                           PE (18:1/18:1)(del9-cis)      C41H78NO8P   
34                                           PE 36:02      C41H78NO8P   
35                           PE (18:1/18:1)(del9-cis)      C41H78NO8P   
36                                    GlcCer 36:01 OH       C42H81NO9   
37                                           PE 36:01      C41H80NO8P   
38                                           SM 36:01     C41H83N2O6P   
39    1,2-Distearoyl-sn-glycero-3-phosphoethanolamine      C41H82NO8P   
40                                           PC 34:03      C42H78NO8P   
41                                 PC (18:1(9Z)/16:0)      C42H82NO8P   
42                        PC (18:1/18:1) (del9-trans)      C44H84NO8P   
43                                           PE 36:01      C41H80NO8P   
44         1,2-Distearoyl-sn-glycero-3-phosphocholine      C44H88NO8P   
45                                    GlcCer 38:01 OH       C44H85NO9   
46                                           PC 34:02      C42H80NO8P   
47                                       PE (O-38:05)      C43H78NO7P   
48                        PC (18:1/18:1) (del9-trans)      C44H84NO8P   
49         1,2-Distearoyl-sn-glycero-3-phosphocholine      C44H88NO8P   
50                                  d7-TG (15:0-18:1)      C51H89D7O6   
51                                           SM 42:02     C47H93N2O6P   
52                                           SM 42:00     C47H97N2O6P   
53                                           PS 36:04     C42H74NO10P   
54                            

We got some matches and we can view their ion images:

In [24]:
image, _  = timsimaging.plotting.image(dataset, i=539, results=results)
show(image)

### Compare with annotation results from METASPACE

In [15]:
metaspace_results = pd.read_csv(r"D:\dataset\Melanie\metaspace_annotations.csv", header=2)

In [32]:
metaspace_ions = metaspace_results[["formula", "adduct"]].copy()
metaspace_ions["adduct"] = metaspace_ions["adduct"].map(lambda x: f"[{x}]".format(x))
timsimaging_ions = final_results[["Neutral.Formula", "Ion.Species"]].copy()
timsimaging_ions.columns = ["formula", "adduct"]
intersection = timsimaging_ions.merge(
    metaspace_ions,
    on=["formula", "adduct"],
    how="inner"
)
intersection

formula  adduct
0  C40H76NO8P   [M+H]
1  C40H80NO8P   [M+H]
2  C39H78NO8P  [M+Na]
3  C40H80NO8P  [M+Na]
4  C41H76NO8P  [M+Na]
5  C41H80NO8P  [M+Na]
6  C41H82NO8P  [M+Na]
7  C42H78NO8P  [M+Na]
8  C42H82NO8P  [M+Na]
9  C48H96NO8P  [M+Na]

![](C40H80NO8P+H.png){#ion image from metaspace width="60%"}